In [1]:
import pandas as pd
import plotly.express as px
import numpy as np

# Configuração para não limitar as linhas exibidas de uma tabela
pd.set_option('display.max_rows', None)

In [2]:
file_male = r"..\educacao_mundial\dataset\mean-years-of-schooling-male.csv"
file_female = r"..\educacao_mundial\dataset\mean-years-of-schooling-female.csv"

In [3]:
dataset4_male = pd.read_csv(file_male)
dataset4_female = pd.read_csv(file_female)

In [9]:
dataset4_male.head()

Entity Code  Year  \
0  Afghanistan  AFG  1975   
1  Afghanistan  AFG  1979   
2      Albania  ALB  2001   
3      Albania  ALB  2008   
4      Albania  ALB  2011   

   UIS: Mean years of schooling (ISCED 1 or higher), population 25+ years, male  
0                                            1.18291                             
1                                            1.48672                             
2                                            9.32291                             
3                                            9.70867                             
4                                           10.33097

In [10]:
# Renomeando o campo de média de anos de estudo
dataset4_male = dataset4_male.rename(
                            columns = {"UIS: Mean years of schooling (ISCED 1 or higher), population 25+ years, male": 
                                       "Average Years"}
                )

dataset4_female = dataset4_female.rename(
                            columns = {"UIS: Mean years of schooling (ISCED 1 or higher), population 25+ years, female": 
                                       "Average Years"}
                )

In [11]:
# Verificando se há campos nulos nos datasets
print("Male: \n", dataset4_male.isnull().sum(), "\n----------------")
print("Female: \n", dataset4_female.isnull().sum(), "\n----------------")

Male: 
 Entity           0
Code             0
Year             0
Average Years    0
dtype: int64 
----------------
Female: 
 Entity           0
Code             0
Year             0
Average Years    0
dtype: int64 
----------------


### Análise da nota do público masculino


Aqui será criado um dataset novo, pois muitos países não possuem registro da nota para alguns anos, enquanto outros países possuem.\
Para contornar o problema, o valor da última nota de um país em um determinado ano, será repetido para o ano seguinte que não possui uma nota até que haja um ano com um novo registro de nota.


In [12]:
# Criando variáveis para identificar o menor e o maior ano do dataset do público masculino
min_year_male = int(dataset4_male["Year"].min())
max_year_male = int(dataset4_male["Year"].max())

min_year_male, max_year_male

(1970, 2019)

In [13]:
# Criando uma série de dados do intervalo entre o menor e maior ano do dataset
every_year_dataset_male = np.arange(min_year_male, max_year_male + 1)
every_year_dataset_male

array([1970, 1971, 1972, 1973, 1974, 1975, 1976, 1977, 1978, 1979, 1980,
       1981, 1982, 1983, 1984, 1985, 1986, 1987, 1988, 1989, 1990, 1991,
       1992, 1993, 1994, 1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002,
       2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013,
       2014, 2015, 2016, 2017, 2018, 2019])

In [14]:
# Criando uma lista de todos os países do dataset
every_country_dataset_male = dataset4_male["Entity"].unique()
#every_country_dataset_male

In [15]:
# Código para criar um dataset onde cada país da lista será atribuído todos os anos possíveis da lista de anos
temp_dataset4_male = pd.DataFrame(
                            [(country, year) for country in every_country_dataset_male for year in every_year_dataset_male], 
                            columns = ["Entity", "Year"]
                    )
temp_dataset4_male.head()

Entity  Year
0  Afghanistan  1970
1  Afghanistan  1971
2  Afghanistan  1972
3  Afghanistan  1973
4  Afghanistan  1974

In [32]:
# Realizando join entre as tabelas, preservando as notas e repetindo a nota para os anos onde não foi avaliado
merged_male = pd.merge(
                temp_dataset4_male, dataset4_male, 
                how = "left", 
                on = ["Entity", "Year"]
         ).sort_values(["Entity", "Year"]).ffill().dropna()
merged_male.head()

Entity  Year Code  Average Years
5  Afghanistan  1975  AFG        1.18291
6  Afghanistan  1976  AFG        1.18291
7  Afghanistan  1977  AFG        1.18291
8  Afghanistan  1978  AFG        1.18291
9  Afghanistan  1979  AFG        1.48672

In [33]:
fig1 = px.choropleth(
    data_frame = merged_male.sort_values(["Year"]),
    locations = "Code",
    color = "Average Years",
    hover_name = "Entity",
    animation_frame = "Year",
    title = "Average Years of Schooling By Year - Male"
)
fig1.update_layout(title_x=0.5)

fig1.show()

### Análise da nota do público feminino
O mesmo processo realizado anteriormente, será realizado para as notas do público feminino

In [23]:
min_year_female = int(dataset4_female["Year"].min())
max_year_female = int(dataset4_female["Year"].max())

In [31]:
every_year_dataset_female = np.arange(min_year_female, max_year_female)
#every_year_dataset_female

every_country_dataset_female = dataset4_female["Entity"].unique()
#every_country_dataset_female

temp_dataset4_female = pd.DataFrame(
                            [(country, year) for country in every_country_dataset_female for year in every_year_dataset_female], 
                            columns = ["Entity", "Year"]
                        )
#temp_dataset4_female.head()

merged_female = pd.merge(
                    temp_dataset4_female, dataset4_female, 
                    how = "left", on = ["Entity", "Year"]
                ).sort_values(["Entity", "Year"]).ffill().dropna()
#merged_female.head(50)

fig2 = px.choropleth(
    data_frame = merged_female.sort_values("Year"),
    locations = "Code",
    hover_name = "Entity",
    color = "Average Years",
    animation_frame = "Year",
    title = "Average Years of Schooling - Female"
)

fig2.update_layout(title_x=0.5)

fig2.show()

### Análise exploratória dos dados

In [34]:
merged_male.head()

Entity  Year Code  Average Years
5  Afghanistan  1975  AFG        1.18291
6  Afghanistan  1976  AFG        1.18291
7  Afghanistan  1977  AFG        1.18291
8  Afghanistan  1978  AFG        1.18291
9  Afghanistan  1979  AFG        1.48672

In [35]:
merged_female.head()

Entity  Year Code  Average Years
5  Afghanistan  1975  AFG        0.21344
6  Afghanistan  1976  AFG        0.21344
7  Afghanistan  1977  AFG        0.21344
8  Afghanistan  1978  AFG        0.21344
9  Afghanistan  1979  AFG        0.15769

In [39]:
merged_male_female = pd.merge(
                        merged_male, merged_female[["Entity", "Year", "Average Years"]],
                        how = "outer",
                        on = ["Entity", "Year"],
                        suffixes = ("_male", "_female")
                     ).sort_values(["Entity", "Year"])

merged_male_female

Entity  Year Code  Average Years_male  \
0                          Afghanistan  1975  AFG             1.18291   
1                          Afghanistan  1976  AFG             1.18291   
2                          Afghanistan  1977  AFG             1.18291   
3                          Afghanistan  1978  AFG             1.18291   
4                          Afghanistan  1979  AFG             1.48672   
5                          Afghanistan  1980  AFG             1.48672   
6                          Afghanistan  1981  AFG             1.48672   
7                          Afghanistan  1982  AFG             1.48672   
8                          Afghanistan  1983  AFG             1.48672   
9                          Afghanistan  1984  AFG             1.48672   
10                         Afghanistan  1985  AFG             1.48672   
11                         Afghanistan  1986  AFG             1.48672   
12                         Afghanistan  1987  AFG             1.48672   
13                         Afghanistan  1988  AFG             1.48672   
14                         Afghanistan  1989  AFG             1.48672   
15                         Afghanistan  1990  AFG             1.48672   
16                         Afghanistan  1991  AFG             1.48672   
17                         Afghanistan  1992  AFG             1.48672   
18                         Afghanistan  1993  AFG             1.48672   
19                         Afghanistan  1994  AFG             1.48672   
20                         Afghanistan  1995  AFG             1.48672   
21                         Afghanistan  1996  AFG             1.48672   
22                         Afghanistan  1997  AFG             1.48672   
23                         Afghanistan  1998  AFG             1.48672   
24                         Afghanistan  1999  AFG             1.48672   
25                         Afghanistan  2000  AFG             1.48672   
26                         Afghanistan  2001  AFG             1.48672   
27                         Afghanistan  2002  AFG             1.48672   
28                         Afghanistan  2003  AFG             1.48672   
29                         Afghanistan  2004  AFG             1.48672   
30                         Afghanistan  2005  AFG             1.48672   
31                         Afghanistan  2006  AFG             1.48672   
32                         Afghanistan  2007  AFG             1.48672   
33                         Afghanistan  2008  AFG             1.48672   
34                         Afghanistan  2009  AFG             1.48672   
35                         Afghanistan  2010  AFG             1.48672   
36                         Afghanistan  2011  AFG             1.48672   
37                         Afghanistan  2012  AFG             1.48672   
38                         Afghanistan  2013  AFG             1.48672   
39                         Afghanistan  2014  AFG             1.48672   
40                         Afghanistan  2015  AFG             1.48672   
41                         Afghanistan  2016  AFG             1.48672   
42                         Afghanistan  2017  AFG             1.48672   
43                         Afghanistan  2018  AFG             1.48672   
44                         Afghanistan  2019  AFG             1.48672   
45                             Albania  1970  AFG             1.48672   
46                             Albania  1971  AFG             1.48672   
47                             Albania  1972  AFG             1.48672   
48                             Albania  1973  AFG             1.48672   
49                             Albania  1974  AFG             1.48672   
50                             Albania  1975  AFG             1.48672   
51                             Albania  1976  AFG             1.48672   
52                             Albania  1977  AFG             1.48672   
53                             Albania  1978  AFG             1.48672   
54               

In [41]:
fig3 = px.line(
        merged_male_female,
        x = "Year",
        y = ["Average Years_male"]
)

fig3.show()